In [12]:
#Everything should work by changing the file paths.. if you think, more processing is need.. let me know
import os, re
from gensim.parsing.preprocessing import remove_stopwords
from nltk.stem import PorterStemmer,SnowballStemmer
from nltk.tokenize import sent_tokenize, word_tokenize
import glob
import codecs
import pandas as pd
import xml.etree.ElementTree as ET

In [3]:
#Data processing 
dir_path = "./AustLit/files/Text/"
out_path = "./AustLit/cleanedfiles/Text_files_cleaned/"
for file in os.listdir(dir_path):
    with open(dir_path+file) as f:
        lines = f.readlines()
        clean_lines = [l.strip() for l in lines if l.strip()]
        data = '\n '.join(clean_lines)
        write_data = re.sub("\&\#[0-9]*\;","",data) 
        write_data = re.sub("[^a-zA-Z]", " ",write_data)
        write_data =' '.join( [w for w in write_data.split() if len(w)>2] )
        write_data = remove_stopwords(write_data.lower())
    if not os.path.exists(out_path):
        os.makedirs(out_path)
    with open(out_path+file, "w") as f:
        f.writelines(write_data)


In [4]:
import nltk

In [5]:
#reading from processed files
#Tokenizing and Stemming process
tokenizer = nltk.data.load('tokenizers/punkt/english.pickle')
file_path = "./AustLit/cleanedfiles/Text_files_cleaned/"
articles_filenames = sorted(glob.glob("./AustLit/cleanedfiles/Text_files_cleaned/*.txt"))


In [6]:
#combining books into one string
corpus_raw = u"/"
for article_filename in articles_filenames:
    print("Reading '{0}'..../".format(article_filename))
    with codecs.open(article_filename, "r", "utf-8/") as artice_file:
            corpus_raw += artice_file.read()
    print("Corpus is now {0} characters long/". format(len(corpus_raw)))
    print()

Reading './AustLit/cleanedfiles/Text_files_cleaned/adaessa-plain.txt'..../
Corpus is now 1 characters long/

Reading './AustLit/cleanedfiles/Text_files_cleaned/adamans-plain.txt'..../
Corpus is now 131600 characters long/

Reading './AustLit/cleanedfiles/Text_files_cleaned/adamaor-plain.txt'..../
Corpus is now 199765 characters long/

Reading './AustLit/cleanedfiles/Text_files_cleaned/adasong-plain.txt'..../
Corpus is now 277079 characters long/

Reading './AustLit/cleanedfiles/Text_files_cleaned/banconf-plain.txt'..../
Corpus is now 677614 characters long/

Reading './AustLit/cleanedfiles/Text_files_cleaned/barmoth-plain.txt'..../
Corpus is now 798977 characters long/

Reading './AustLit/cleanedfiles/Text_files_cleaned/barsequ-plain.txt'..../
Corpus is now 897474 characters long/

Reading './AustLit/cleanedfiles/Text_files_cleaned/barstev-plain.txt'..../
Corpus is now 1117261 characters long/

Reading './AustLit/cleanedfiles/Text_files_cleaned/barstra-plain.txt'..../
Corpus is now 119

In [7]:
raw_sentences = tokenizer.tokenize(corpus_raw)
nouns = [] #empty to array to hold all nouns

for sentence in raw_sentences:
     for word,pos in nltk.pos_tag(nltk.word_tokenize(str(sentence))):
         if (pos == 'NN' or pos == 'NNP' or pos == 'NNS' or pos == 'NNPS'):
             nouns.append(word)

In [11]:
print (nouns)

['essays', 'william', 'inglis', 'amp', 'matthew', 'england', 'master', 'boy', 'watches', 'bird', 'swoop', 'quarry', 'cries', 'flight', 'sheer', 'joy', 'voice', 'sea', 'winds', 'waves', 'acknowledgment', 'honour', 'sovran', 'truth', 'contents', 'preface', 'civilization', 'poetry', 'adam', 'salvation', 'army', 'sydney', 'civilization', 'culture', 'dawnwards', 'dialogue', 'introduction', 'iii', 'preface', 'readers', 'book', 'characters', 'man', 'admiration', 'respect', 'reality', 'beg', 'hope', 'state', 'honour', 'acquaintancenay', 'himi', 'charges', 'personality', 'characters', 'people', 'originals', 'theory', 'mystification', 'author', 'occupation', 'author', 'man', 'life', 'use', 'analysts', 'critics', 'life', 'form', 'reflection', 'form', 'example', 'book', 'lothair', 'endymion', 'characters', 'men', 'men', 'events', 'criticism', 'time', 'rest', 'attempt', 'mystification', 'materials', 'hand', 'regards', 'essays', 'point', 'course', 'intention', 'impugn', 'competency', 'press', 'deal'

In [10]:
def sentence_to_wordlist(raw):
    stemmer = SnowballStemmer('english')
    words = raw.split()
    stem_words = ' '.join([stemmer.stem(word) for word in words])
    return stem_words

In [13]:
sentences = []
for raw_sentence in nouns:
    if len(raw_sentence) > 0:
        sentences.append(sentence_to_wordlist(raw_sentence))

In [14]:
print(sentence_to_wordlist(raw_sentences[0]))


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [15]:
token_count = sum([len(sentence) for sentence in sentences])
print("The book corpus contains {0:,} tokens".format(token_count))

The book corpus contains 4,210,735 tokens


In [18]:
#This created a dataframe with Author, Date and processed text....Not so happy with this code though :(
def text_to_pandas(txtfile_path, file_name):
    out_table_path = "./AustLit/cleanedfiles/text_table_files/"
    tree = ET.parse(txtfile_path)
    root = tree.getroot()
    data={}
    for author in root.iter("author"):
        data["Author"]=author.text
    #for date in root.find("./teiHeader/profileDesc/creation"):
    date = root.find("./teiHeader/profileDesc/creation/date")
    if date is not None:
        data["Date"]=date.text
    df_xml = pd.DataFrame(data,index=[0])
    file_name = file_name.split("-")[0]
    file_name = file_name+"-plain.txt"
    with open(os.path.join("./AustLit/cleanedfiles/Text_files_cleaned/", file_name), 'r') as f:
        df_xml['Text'] = f.read()
    if not os.path.exists(out_table_path):
        os.makedirs(out_table_path)
    df_xml.to_csv(os.path.join(out_table_path,file_name), sep='\t')
    return

In [19]:
xml_path = "./AustLit/files/Raw/"
for file in os.listdir(xml_path):
    to_pd_path = os.path.join(xml_path, file)
    text_to_pandas(to_pd_path, file)